# Moses IS-EN EN-IS phrase þýðingarvél
Sjá `README.md` til þess að keyra þetta vélrit (e. notebook).

Í þessu vélriti eru gögn forunnin og Moses þýðingarkerfið notað til þess búa til tvö þýðingarkerfi, IS-EN og EN-IS.
Það er gert ráð fyrir því að öll gögn séu aðgengileg undir `/work/data`. Sjá leiðbeiningar í `README.md` um hvernig það er gert með `docker` eða `singularity`.

Í stuttu máli skiptist vélritið í eftirfarandi þætti:
1. Samhliða og einhliða gögn undirbúin.
1. Tungumála módel byggt fyrir EN og IS (KenLM).
1. Texta skipt í þrjá hluta; train/val/test, fjöldi setninga í val/test er 3000/2000.
1. Moses kerfið þjálfað með train hluta texta.
1. Moses kerfið fínpússað með val hluta texta.
1. Moses kerfið metið með BLEU mælingin á test hluta texta.

Allar skrár og líkön eru raðað í skrána "WORKING_DIR" (sjá `README.md`).

Safnið `corpus.py` skilgreinir föll og gagnategundir sem eru mikið nýttar hér.

In [2]:
from collections import defaultdict, Counter, OrderedDict
import os
import pathlib
from pathlib import Path
import re
from pprint import pprint
import importlib
from typing import List

import matplotlib.pyplot as plt
import numpy as np

import corpus.corpus as c

importlib.reload(c)

%matplotlib notebook

working_dir = pathlib.Path('/work')
data_dir = working_dir.joinpath('data')

[nltk_data] Downloading package punkt to
[nltk_data]     /home/staff/haukurpj/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /home/staff/haukurpj/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


Let's be sure that Moses is installed and the data is there.

In [3]:
print(os.getenv('MOSESDECODER'))
print(os.getenv('MOSESDECODER_TOOLS'))
print(int(os.getenv('THREADS')))
!ls {data_dir}

/opt/moses
/opt/moses_tools
14
bin  parice  risamalheild


In [4]:
# List of stages in processing
CAT = 'cat'
SHUFFLE = 'shuffle'
REGEXP = 'regexp'
SENT_FIX = 'sent_fix'
LOWER = 'lower'
TOKENIZE = 'tok'
PLACEHOLDERS = 'placeholders'
LENGTH = 'length'
LM = 'lm-blm'
TRAIN = 'train'
TEST = 'test'
VAL = 'val'
TRANSLATED_EN_IS = 'translated_en_is'
TRANSLATED_IS_EN = 'translated_is_en'

parice_dir = data_dir.joinpath('parice')
rmh_dir = data_dir.joinpath('risamalheild')
train_parice_dir = parice_dir.joinpath('train')
test_parice_dir = parice_dir.joinpath('test')
val_parice_dir = parice_dir.joinpath('val')

!mkdir -p {train_parice_dir}
!mkdir -p {test_parice_dir}
!mkdir -p {val_parice_dir}

pipeline = [
    SHUFFLE,
    LOWER, 
    REGEXP, 
    TOKENIZE,
    PLACEHOLDERS,
    LENGTH,
    LM,
    TRANSLATED_EN_IS,
    TRANSLATED_IS_EN
]
rmh_stages = [
    SENT_FIX,
    LOWER,
    REGEXP,
    TOKENIZE,
    PLACEHOLDERS,
    LM,
    CAT
]
parice_pipeline = [
    CAT,
    SENT_FIX,
    SHUFFLE
]

# If we are not starting from scratch - we try to load all intermediary stages
en_parice = c.pipeline_load(parice_dir, parice_pipeline, c.Lang.EN)
is_parice = c.pipeline_load(parice_dir, parice_pipeline, c.Lang.IS)
en_train = c.pipeline_load(train_parice_dir, pipeline, c.Lang.EN)
is_train = c.pipeline_load(train_parice_dir, pipeline, c.Lang.IS)
en_test = c.pipeline_load(test_parice_dir, pipeline, c.Lang.EN)
is_test = c.pipeline_load(test_parice_dir, pipeline, c.Lang.IS)
en_val = c.pipeline_load(val_parice_dir, pipeline, c.Lang.EN)
is_val = c.pipeline_load(val_parice_dir, pipeline, c.Lang.IS)
rmh = c.pipeline_load(rmh_dir, rmh_stages, c.Lang.IS)
pprint(en_parice)
pprint(is_parice)
pprint(rmh)
pprint(en_train)
pprint(is_train)

{'cat': PosixPath('/work/data/parice/cat.en'),
 'sent_fix': PosixPath('/work/data/parice/sent_fix.en'),
 'shuffle': PosixPath('/work/data/parice/shuffle.en')}
{'cat': PosixPath('/work/data/parice/cat.is'),
 'sent_fix': PosixPath('/work/data/parice/sent_fix.is'),
 'shuffle': PosixPath('/work/data/parice/shuffle.is')}
{'cat': None,
 'lm-blm': None,
 'lower': PosixPath('/work/data/risamalheild/lower.is'),
 'placeholders': None,
 'regexp': PosixPath('/work/data/risamalheild/regexp.is'),
 'sent_fix': PosixPath('/work/data/risamalheild/sent_fix.is'),
 'tok': PosixPath('/work/data/risamalheild/tok.is')}
{'length': None,
 'lm-blm': None,
 'lower': PosixPath('/work/data/parice/train/lower.en'),
 'placeholders': None,
 'regexp': PosixPath('/work/data/parice/train/regexp.en'),
 'shuffle': PosixPath('/work/data/parice/train/shuffle.en'),
 'tok': PosixPath('/work/data/parice/train/tok.en'),
 'translated_en_is': None,
 'translated_is_en': None}
{'length': None,
 'lm-blm': None,
 'lower': PosixPath('

### Stytta þjálfunarsetningar
Moses á erfitt með að samstilla langar setningar. Við styttum þjálfunarsetningarnar svo einungis setningar sem eru eitt orð eða lengri upp að tölunni sem er skilgreint að neðan. Við höfum tekið eftir því að niðurstöðurnar sem við fáum með hámarkslengd (100) gefa ekki góðar niðurstöður.

Þar sem við notum fall sem er skilgreint í Moses og tekur inn tvær skrár í einu fer nafnavenjan eitthvað á flakk.

In [7]:
def corpus_shorten(path, path_out, lang_id_1, lang_id_2, min_length, max_length):
    !{os.getenv('MOSESDECODER')}/scripts/training/clean-corpus-n.perl {path} {lang_id_1} {lang_id_2} {path_out} {min_length} {max_length}
    return True

path_out = is_train[REGEXP].with_name(LENGTH)
path = is_train[REGEXP].parent.joinpath(REGEXP)
corpus_shorten(path, path_out, 'en', 'is', 1, 70)

is_train[LENGTH] = is_train[REGEXP].with_name(LENGTH).with_suffix('.is')
en_train[LENGTH] = en_train[REGEXP].with_name(LENGTH).with_suffix('.en')

perl: warning: Setting locale failed.
perl: warning: Please check that your locale settings:
	LANGUAGE = "en_US:en",
	LC_ALL = (unset),
	LC_CTYPE = "C.UTF-8",
	LANG = "en_US.UTF-8"
    are supported and installed on your system.
perl: warning: Falling back to the standard locale ("C").
clean-corpus.perl: processing /work/data/parice/train/regexp.en & .is to /work/data/parice/train/length, cutoff 1-70, ratio 9
..........(100000)..........(200000)..........(300000)..........(400000)..........(500000)..........(600000)..........(700000)..........(800000)..........(900000)..........(1000000)..........(1100000)..........(1200000)..........(1300000)..........(1400000)..........(1500000)..........(1600000)..........(1700000)..........(1800000)..........(1900000)..........(2000000)..........(2100000)..........(2200000)..........(2300000)..........(2400000)..........(2500000)..........(2600000)..........(2700000)..........(2800000)..........(2900000)..........(3000000)..........(3100000).......

### Tungumála módel
Við búum til KenLM mállíkan til þess að gefa okkur líkindi setninga. Til að flýta uppflettingum þá tungumála módelið samtímis kjörsniðið.

In [8]:
def create_lm(path, out_path, order):
    tmp_arpa = c.corpus_create_path(path, 'arpa')
    !{os.getenv('MOSESDECODER')}/bin/lmplz --order {order} --temp_prefix {data_dir}/ --memory 70% < {path} > {tmp_arpa}
    !{os.getenv('MOSESDECODER')}/bin/build_binary -S 70% {tmp_arpa} {out_path}
    return True

In [9]:
is_train[LM] = c.corpus_create_path(is_train[REGEXP], LM)
en_train[LM] = c.corpus_create_path(en_train[REGEXP], LM)

create_lm(is_train[REGEXP], is_train[LM], order=3)
create_lm(en_train[REGEXP], en_train[LM], order=3)

=== 1/5 Counting and sorting n-grams ===
Reading /work/data/parice/train/regexp.is
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
****************************************************************************************************
Unigram tokens 46731475 types 630451
=== 2/5 Calculating and sorting adjusted counts ===
Chain sizes: 1:7565412 2:32821549056 3:61540405248
Statistics:
1 630451 D1=0.660768 D2=1.06844 D3+=1.40048
2 5484670 D1=0.745842 D2=1.11552 D3+=1.42122
3 14030141 D1=0.703343 D2=1.17946 D3+=1.46906
Memory estimate for binary LM:
type     MB
probing 382 assuming -p 1.5
probing 415 assuming -r models -p 1.5
trie    169 without quantization
trie    100 assuming -q 8 -b 8 quantization 
trie    159 assuming -a 22 array pointer compression
trie     90 assuming -a 22 -q 8 -b 8 array pointer compression and quantization
=== 3/5 Calculating and sorting initial probabilities ===
Chain sizes: 1:7565412 2:87754720 3:280602820
----

True

### Sameina RMH og IS ParIce fyrir mállíkan

In [64]:
rmh_pipeline[CAT] = c.corpus_create_path(rmh_pipeline[PLACEHOLDERS], CAT)
c.corpora_combine((is_parice_pipeline[PLACEHOLDERS], rmh_pipeline[PLACEHOLDERS]), rmh_pipeline[CAT])

True

Búa til mállíkan.

In [73]:
rmh_pipeline[LM] = c.corpus_create_path(rmh_pipeline[CAT], LM)

create_lm(rmh_pipeline[CAT], rmh_pipeline[LM], order=3)

=== 1/5 Counting and sorting n-grams ===
Reading /work/data/rmh/cat.is
----5---10---15---20---25---30---35---40---45---50---55---60---65---70---75---80---85---90---95--100
****************************************************************************************************
Unigram tokens 1326157081 types 5788599
=== 2/5 Calculating and sorting adjusted counts ===
Chain sizes: 1:69463188 2:32800022528 3:61500043264
Statistics:
1 5788599 D1=0.699446 D2=1.03942 D3+=1.33338
2 91612672 D1=0.755001 D2=1.07806 D3+=1.34462
3 341746400 D1=0.700042 D2=1.30801 D3+=1.52644
Memory estimate for binary LM:
type      MB
probing 8106 assuming -p 1.5
probing 8653 assuming -r models -p 1.5
trie    3588 without quantization
trie    2138 assuming -q 8 -b 8 quantization 
trie    3368 assuming -a 22 array pointer compression
trie    1918 assuming -a 22 -q 8 -b 8 array pointer compression and quantization
=== 3/5 Calculating and sorting initial probabilities ===
Chain sizes: 1:69463188 2:1465802752 3:683492800

True

Prófa tungumála módel, það ættu ekki að vera nein óþekkt orð.

In [10]:
def eval_sentence(lm_model, sentence):
   !echo "{sentence}" | {os.getenv('MOSESDECODER')}/bin/query {lm_model}

eval_sentence(is_train[LM], "þetta er flott íslensk setning , er það ekki ?")
eval_sentence(en_train[LM], "this is a nice english sentence , right ?")

þetta=427 2 -1.9087273	er=108 3 -0.25079718	flott=7282 3 -2.4735093	íslensk=8557 1 -6.074996	setning=40525 1 -6.0030327	,=25 2 -1.7541713	er=108 2 -2.1018214	það=269 3 -0.9875311	ekki=193 3 -0.7616743	?=97 3 -0.82043517	</s>=2 3 -0.010254155	Total: -23.146952 OOV: 0
Perplexity including OOVs:	127.1359387448515
Perplexity excluding OOVs:	127.1359387448515
OOVs:	0
Tokens:	11
Name:query	VmPeak:411536 kB	VmRSS:4848 kB	RSSMax:396028 kB	user:0.003832	sys:0.065156	CPU:0.068988	real:0.127266
this=207 2 -1.8216469	is=200 3 -0.6768345	a=12 3 -0.99623716	nice=1080 3 -2.86407	english=4893 1 -4.508677	sentence=3081 1 -5.0882697	,=6 2 -1.1383297	right=182 2 -3.7728295	?=94 3 -0.14291577	</s>=2 3 -0.034210734	Total: -21.044022 OOV: 0
Perplexity including OOVs:	127.17512133209536
Perplexity excluding OOVs:	127.17512133209536
OOVs:	0
Tokens:	10
Name:query	VmPeak:323864 kB	VmRSS:5100 kB	RSSMax:308608 kB	user:0.00382	sys:0.038201	CPU:0.042021	real:0.0398345


## Moses þjálfunar föll
Næstu föll snúa að þjálfun Moses og annarra atriða sem þarf að hafa í huga. Þjálfunin tekur um 12 klst.
Til þess að sjá framgang þjálfunar - sjá útprent þegar kallað er í föllin. Síðasta skrefið metur þýðingar Moses.

In [11]:
def train_moses(model_dir, corpus, lang_from, lang_to, lang_to_lm):
    print(f'tail -f {model_dir}/training.out')
    result = !{os.getenv('MOSESDECODER')}/scripts/training/train-model.perl -root-dir {model_dir} \
        -corpus {corpus} \
        -f {lang_from} -e {lang_to} \
        -alignment grow-diag-final-and -reordering msd-bidirectional-fe \
        -lm 0:3:{lang_to_lm}:8 \
        -mgiza -mgiza-cpus {os.getenv('THREADS')} \
        -cores {os.getenv('THREADS')} \
        -external-bin-dir {os.getenv('MOSESDECODER_TOOLS')} &> {model_dir}/training.out
    return model_dir

In [12]:
def tune_moses(model_dir, corpus_val_from, corpus_val_to, base_moses_ini):
    print(f'tail -f {model_dir}/tune.out')
    result = !{os.getenv('MOSESDECODER')}/scripts/training/mert-moses.pl \
        {corpus_val_from} \
        {corpus_val_to} \
        {os.getenv('MOSESDECODER')}/bin/moses {base_moses_ini} \
        --mertdir {os.getenv('MOSESDECODER')}/bin \
        --working-dir {model_dir} \
        --decoder-flags="-threads {os.getenv('THREADS')}" &> {model_dir}/tune.out
    return model_dir

In [13]:
def prepare_binarisation(tuned_moses_ini,
                         lm_path_in,
                         lm_path_out,
                         binarised_moses_ini,
                         binarised_phrase_table,
                         binarised_reordering_table):
    !cp {tuned_moses_ini} {binarised_moses_ini}
    !cp {lm_path_in} {lm_path_out}
    # Adjust the path in the moses.ini file to point to the new files.
    escaped_path_in = str(lm_path_in).replace(r'/', '\/')
    escaped_path_out = str(lm_path_out).replace(r'/', '\/')
    !sed -i 's/{escaped_path_in}/{escaped_path_out}/' {binarised_moses_ini}
    # Adjust the path in the moses.ini file to point to the new files.
    escaped_path = str(binarised_phrase_table).replace(r'/', '\/')
    !sed -i 's/PhraseDictionaryMemory/PhraseDictionaryCompact/' {binarised_moses_ini}
    !sed -i 's/4 path=.*\.gz input-factor/4 path={escaped_path} input-factor/' {binarised_moses_ini}
    # Adjust the path in the moses.ini file
    escaped_path = str(binarised_reordering_table).replace(r'/', '\/')
    !sed -i 's/0 path=.*\.gz$/0 path={escaped_path}/' {binarised_moses_ini}
    
def binarise_phrase_table(base_phrase_table, binarised_phrase_table):
    #Create the table
    !{os.getenv('MOSESDECODER')}/bin/processPhraseTableMin \
        -in {base_phrase_table} \
        -nscores 4 \
        -out {binarised_phrase_table}
    
def binarise_reordering_table(base_reordering_table, binarised_reordering_table):
    #Create the table
    !{os.getenv('MOSESDECODER')}/bin/processLexicalTableMin \
        -in {base_reordering_table} \
        -out {binarised_reordering_table}

In [14]:
# It only makes sense to filter the model when you know what text the system needs to translate.
def filter_model(out_dir, moses_ini, corpus):
    !{os.getenv('MOSESDECODER')}/scripts/training/filter-model-given-input.pl {out_dir} {moses_ini} {corpus}


In [15]:
def translate_corpus(moses_ini, corpus, corpus_translated):
    !{os.getenv('MOSESDECODER')}/bin/moses \
        -f {moses_ini} < {corpus} > {corpus_translated}
    
def eval_translation(corpus_gold, corpus_translated):
    result = !{os.getenv('MOSESDECODER')}/scripts/generic/multi-bleu.perl -lc {corpus_gold} < {corpus_translated}
    return result 

### EN-IS þýðingarvél

In [16]:
base_model_dir = working_dir.joinpath('en-is/base')
tuned_model_dir = working_dir.joinpath('en-is/tuned')
binarised_model_dir = working_dir.joinpath('en-is/binarised')

base_moses_ini = base_model_dir.joinpath('model/moses.ini')
base_phrase_table = base_model_dir.joinpath('model/phrase-table.gz')
base_reordering_table = base_model_dir.joinpath('model/reordering-table.wbe-msd-bidirectional-fe.gz')

tuned_moses_ini = tuned_model_dir.joinpath('moses.ini')

binarised_moses_ini = binarised_model_dir.joinpath('moses.ini')
binarised_phrase_table = binarised_model_dir.joinpath('phrase-table')
binarised_reordering_table = binarised_model_dir.joinpath('reordering-table')

Þjálfa

In [ ]:
!mkdir -p {base_model_dir}

path = is_train[LENGTH].parent.joinpath(LENGTH)

train_moses(base_model_dir, path, 'en', 'is', is_train[LM])

tail -f /work/en-is/base/training.out


Fínpússa

In [ ]:
!mkdir -p {tuned_model_dir}

tune_moses(tuned_model_dir, en_val[REGEXP], is_val[REGEXP], base_moses_ini)

Pakka saman

In [ ]:
!mkdir -p {binarised_model_dir}

lm_in = is_train[LM]
lm_out = binarised_model_dir.joinpath('lm-is.blm')

prepare_binarisation(tuned_moses_ini, 
                     lm_in,
                     lm_out, 
                     binarised_moses_ini, 
                     binarised_phrase_table, 
                     binarised_reordering_table)
binarise_phrase_table(base_phrase_table, binarised_phrase_table)
binarise_reordering_table(base_reordering_table, binarised_reordering_table)

Þýða test gögnin og meta þýðingu

In [16]:
en_test[TRANSLATED_EN_IS] = c.corpus_create_path(en_test[REGEXP], TRANSLATED_EN_IS)

translate_corpus(binarised_moses_ini,  en_test[REGEXP], en_test[TRANSLATED_EN_IS])
print(eval_translation(is_test[REGEXP], en_test[TRANSLATED_EN_IS]))


Defined parameters (per moses.ini or switch):
	config: /work/en-is/binarised/moses.ini 
	distortion-limit: 6 
	feature: UnknownWordPenalty WordPenalty PhrasePenalty PhraseDictionaryCompact name=TranslationModel0 num-features=4 path=/work/en-is/binarised/phrase-table input-factor=0 output-factor=0 LexicalReordering name=LexicalReordering0 num-features=6 type=wbe-msd-bidirectional-fe-allff input-factor=0 output-factor=0 path=/work/en-is/binarised/reordering-table Distortion KENLM name=LM0 factor=0 path=/work/en-is/binarised/lm-is.blm order=3 
	input-factors: 0 
	mapping: 0 T 0 
	threads: 14 
	weight: LexicalReordering0= 0.0289401 0.00216597 0.102201 0.0376488 -0.0181822 0.0658433 Distortion0= 0.0166935 LM0= 0.149235 WordPenalty0= -0.204966 PhrasePenalty0= 0.126341 TranslationModel0= 0.0991475 0.0160094 0.128108 0.00451765 UnknownWordPenalty0= 1 
line=UnknownWordPenalty
FeatureFunction: UnknownWordPenalty0 start: 0 end: 0
line=WordPenalty
FeatureFunction: WordPenalty0 start: 1 end: 1
line

Line 9: Collecting options took 3.281 seconds at moses/Manager.cpp Line 141
Line 9: Search took 0.041 seconds
Line 9: Decision rule took 0.000 seconds total
Line 9: Additional reporting took 0.000 seconds total
Line 9: Translation took 3.324 seconds total
Translating: it ' s dead out there . 
Line 25: Initialize search took 0.000 seconds total
Line 25: Collecting options took 0.830 seconds at moses/Manager.cpp Line 141
Line 6: Collecting options took 4.171 seconds at moses/Manager.cpp Line 141
Line 24: Collecting options took 1.453 seconds at moses/Manager.cpp Line 141
Line 25: Search took 0.114 seconds
Line 25: Decision rule took 0.000 seconds total
Line 25: Additional reporting took 0.000 seconds total
Line 25: Translation took 0.944 seconds total
Translating: • the employer demonstrates that workers are still protected against adverse health effects and against safety risks , including by ensuring that the instructions for safe use provided by the manufacturer in accordance with cou

Line 30: Search took 0.373 seconds
Line 30: Decision rule took 0.000 seconds total
Line 30: Additional reporting took 0.000 seconds total
Line 30: Translation took 3.286 seconds total
Translating: as a minimum , tier 4 as defined in annex xii shall be applied . 
Line 43: Initialize search took 0.000 seconds total
Line 29: Collecting options took 3.395 seconds at moses/Manager.cpp Line 141
Line 10: Collecting options took 8.124 seconds at moses/Manager.cpp Line 141
Line 29: Search took 0.121 seconds
Line 29: Decision rule took 0.000 seconds total
Line 29: Additional reporting took 0.000 seconds total
Line 29: Translation took 3.516 seconds total
Translating: if i show you a picture , can you confirm it ? 
Line 44: Initialize search took 0.000 seconds total
Line 42: Collecting options took 0.610 seconds at moses/Manager.cpp Line 141
Line 42: Search took 0.320 seconds
Line 42: Decision rule took 0.000 seconds total
Line 42: Additional reporting took 0.000 seconds total
Line 42: Translatio

Line 44: Search took 0.277 seconds
Line 44: Decision rule took 0.000 seconds total
Line 44: Additional reporting took 0.000 seconds total
Line 44: Translation took 3.362 seconds total
Translating: sampling points should in general be sited so as to avoid measuring very small micro-environments in their immediate vicinity . 
Line 66: Initialize search took 0.000 seconds total
Line 63: Collecting options took 0.252 seconds at moses/Manager.cpp Line 141
Line 57: Collecting options took 0.701 seconds at moses/Manager.cpp Line 141
Line 65: Collecting options took 0.203 seconds at moses/Manager.cpp Line 141
Line 63: Search took 0.061 seconds
Line 63: Decision rule took 0.000 seconds total
Line 63: Additional reporting took 0.000 seconds total
Line 63: Translation took 0.314 seconds total
Translating: vitamin d 
Line 67: Initialize search took 0.000 seconds total
Line 67: Collecting options took 0.014 seconds at moses/Manager.cpp Line 141
Line 67: Search took 0.002 seconds
Line 67: Decision r

Line 69: Collecting options took 2.170 seconds at moses/Manager.cpp Line 141
Line 81: Collecting options took 1.186 seconds at moses/Manager.cpp Line 141
Line 66: Collecting options took 2.476 seconds at moses/Manager.cpp Line 141
Line 83: Search took 0.234 seconds
Line 83: Decision rule took 0.000 seconds total
Line 83: Additional reporting took 0.000 seconds total
Line 83: Translation took 1.108 seconds total
Translating: uncommon ( affects 1 to 10 users in 1,000 ) : 
Line 88: Initialize search took 0.000 seconds total
Line 81: Search took 0.097 seconds
Line 81: Decision rule took 0.000 seconds total
Line 81: Additional reporting took 0.000 seconds total
Line 81: Translation took 1.282 seconds total
Translating: type 
Line 89: Initialize search took 0.000 seconds total
Line 74: Collecting options took 1.747 seconds at moses/Manager.cpp Line 141
Line 89: Collecting options took 0.012 seconds at moses/Manager.cpp Line 141
Line 89: Search took 0.000 seconds
Line 89: Decision rule took 0

...

Line 2944: Collecting options took 0.111 seconds at moses/Manager.cpp Line 141
Line 2945: Collecting options took 0.112 seconds at moses/Manager.cpp Line 141
Line 2932: Search took 0.411 seconds
Line 2932: Decision rule took 0.000 seconds total
Line 2932: Additional reporting took 0.000 seconds total
Line 2932: Translation took 0.625 seconds total
Translating: • refrigeration and air-conditioning equipment and products which contain chlorofluorocar- bons used as refrigerants , or whose continuing function relies on the supply of chlorofluoro- carbons used as refrigerants , in other equip- ment and products ; 
Line 2947: Initialize search took 0.002 seconds total
Line 2942: Collecting options took 0.170 seconds at moses/Manager.cpp Line 141
Line 2946: Collecting options took 0.176 seconds at moses/Manager.cpp Line 141
Line 2942: Search took 0.142 seconds
Line 2942: Decision rule took 0.000 seconds total
Line 2942: Additional reporting took 0.000 seconds total
Line 2942: Translation took

Line 2962: Collecting options took 0.003 seconds at moses/Manager.cpp Line 141
Line 2962: Search took 0.000 seconds
Line 2962: Decision rule took 0.000 seconds total
Line 2962: Additional reporting took 0.000 seconds total
Line 2962: Translation took 0.003 seconds total
Translating: the cooperation agreement concluded between esma and mas provides for information exchange with regard to enforcement and supervisory measures taken against cross border cras . 
Line 2963: Initialize search took 0.000 seconds total
Line 2959: Collecting options took 0.070 seconds at moses/Manager.cpp Line 141
Line 2961: Collecting options took 0.060 seconds at moses/Manager.cpp Line 141
Line 2963: Collecting options took 0.116 seconds at moses/Manager.cpp Line 141
Line 2948: Search took 0.469 seconds
Line 2948: Decision rule took 0.000 seconds total
Line 2948: Additional reporting took 0.000 seconds total
Line 2948: Translation took 0.691 seconds total
Line 2955: Collecting options took 0.403 seconds at mos

Line 2947: Search took 0.870 seconds
Line 2947: Decision rule took 0.000 seconds total
Line 2947: Additional reporting took 0.000 seconds total
Line 2947: Translation took 1.237 seconds total
Translating: scanning . 
Line 2971: Initialize search took 0.000 seconds total
Line 2969: Search took 0.247 seconds
Line 2969: Decision rule took 0.000 seconds total
Line 2969: Additional reporting took 0.000 seconds total
Line 2969: Translation took 0.295 seconds total
Line 2970: Search took 0.079 seconds
Line 2970: Decision rule took 0.000 seconds total
Line 2970: Additional reporting took 0.000 seconds total
Line 2970: Translation took 0.084 seconds total
Line 2971: Collecting options took 0.003 seconds at moses/Manager.cpp Line 141
Translating: united states 
Line 2972: Initialize search took 0.000 seconds total
Line 2971: Search took 0.002 seconds
Line 2971: Decision rule took 0.000 seconds total
Line 2971: Additional reporting took 0.000 seconds total
Line 2971: Translation took 0.005 second

Line 2964: Search took 0.610 seconds
Line 2964: Decision rule took 0.000 seconds total
Line 2964: Additional reporting took 0.000 seconds total
Line 2964: Translation took 0.743 seconds total
Line 2977: Search took 0.189 seconds
Line 2977: Decision rule took 0.000 seconds total
Line 2977: Additional reporting took 0.000 seconds total
Line 2977: Translation took 0.269 seconds total
Translating: liver 
Line 2986: Initialize search took 0.000 seconds total
Translating: this is gulick in the blue suit , the state senator . 
Line 2987: Initialize search took 0.001 seconds total
Line 2986: Collecting options took 0.006 seconds at moses/Manager.cpp Line 141
Line 2986: Search took 0.000 seconds
Line 2986: Decision rule took 0.000 seconds total
Line 2986: Additional reporting took 0.000 seconds total
Line 2986: Translation took 0.006 seconds total
Translating: ‘bg : 
Line 2989: Initialize search took 0.000 seconds total
Translating: co-administration of efavirenz with atazanavir/ritonavir is no

Line 2982: Search took 0.972 seconds
BEST TRANSLATION: tilskipun 2006 / 87 / eb ( 4 ) - meðferð veitir framkvæmdastjórninni heimild til að aðlaga þessar tæknilegu kröfur í ljósi tækniframfara og þróunar vegna vinnu annarra alþjóðastofnana , einkum að ccnr , i . [11111111111111111111111111111111111111]  [total=-19.421] core=(0.000,-36.000,15.000,-27.672,-58.033,-14.849,-67.773,-4.607,-7.069,-1.946,-7.709,-3.045,-1.806,-10.000,-147.056)  
BEST TRANSLATION: hýdróklórtíazíð getur valdið eða aukið blóðþurrð sem getur valdið saltaröskun ( sjá kafla 4.4 ) . [111111111111111111]  [total=-4.337] core=(0.000,-16.000,8.000,-0.540,-26.415,-0.506,-18.296,-1.600,0.000,0.000,-1.263,0.000,0.000,0.000,-53.003)  
BEST TRANSLATION: vinnukonan . [111]  [total=-2.544] core=(0.000,-2.000,1.000,0.000,-2.522,-1.099,-4.401,-0.336,0.000,0.000,0.000,0.000,0.000,0.000,-19.228)  
BEST TRANSLATION: við erum ekki að tala um ekki neitt . [11111111]  [total=-3.327] core=(0.000,-9.000,3.000,-4.982,-19.633,-4.138,-13.49

### Demo
Þýða einhvern texta.

In [6]:
def translate_en_is(moses_ini, sentence):
    sentence = c.sent_process_v1(sentence, c.Lang.EN)
    !echo "{sentence}" | {os.getenv('MOSESDECODER')}/bin/moses -f {moses_ini}

In [10]:
sentence = "English sentence."
print(translate_en_is(binarised_moses_ini, sentence))

Defined parameters (per moses.ini or switch):
	config: /work/en-is/binarised/moses.ini 
	distortion-limit: 6 
	feature: UnknownWordPenalty WordPenalty PhrasePenalty PhraseDictionaryCompact name=TranslationModel0 num-features=4 path=/work/en-is/binarised/phrase-table input-factor=0 output-factor=0 LexicalReordering name=LexicalReordering0 num-features=6 type=wbe-msd-bidirectional-fe-allff input-factor=0 output-factor=0 path=/work/en-is/binarised/reordering-table Distortion KENLM name=LM0 factor=0 path=/work/en-is/binarised/lm-is.blm order=3 
	input-factors: 0 
	mapping: 0 T 0 
	threads: 14 
	weight: LexicalReordering0= 0.0289401 0.00216597 0.102201 0.0376488 -0.0181822 0.0658433 Distortion0= 0.0166935 LM0= 0.149235 WordPenalty0= -0.204966 PhrasePenalty0= 0.126341 TranslationModel0= 0.0991475 0.0160094 0.128108 0.00451765 UnknownWordPenalty0= 1 
line=UnknownWordPenalty
FeatureFunction: UnknownWordPenalty0 start: 0 end: 0
line=WordPenalty
FeatureFunction: WordPenalty0 start: 1 end: 1
line

In [8]:
sentence = "The event was created by Matty Roberts , [ 1 ] who confirmed it was comedic and disavowed responsibility for any casualties if people actually attempt to raid the military base."
print(translate_en_is(binarised_moses_ini, sentence))

Defined parameters (per moses.ini or switch):
	config: /work/en-is/binarised/moses.ini 
	distortion-limit: 6 
	feature: UnknownWordPenalty WordPenalty PhrasePenalty PhraseDictionaryCompact name=TranslationModel0 num-features=4 path=/work/en-is/binarised/phrase-table input-factor=0 output-factor=0 LexicalReordering name=LexicalReordering0 num-features=6 type=wbe-msd-bidirectional-fe-allff input-factor=0 output-factor=0 path=/work/en-is/binarised/reordering-table Distortion KENLM name=LM0 factor=0 path=/work/en-is/binarised/lm-is.blm order=3 
	input-factors: 0 
	mapping: 0 T 0 
	threads: 14 
	weight: LexicalReordering0= 0.0289401 0.00216597 0.102201 0.0376488 -0.0181822 0.0658433 Distortion0= 0.0166935 LM0= 0.149235 WordPenalty0= -0.204966 PhrasePenalty0= 0.126341 TranslationModel0= 0.0991475 0.0160094 0.128108 0.00451765 UnknownWordPenalty0= 1 
line=UnknownWordPenalty
FeatureFunction: UnknownWordPenalty0 start: 0 end: 0
line=WordPenalty
FeatureFunction: WordPenalty0 start: 1 end: 1
line

### IS-EN þýðingarvél

In [25]:
base_model_dir = working_dir.joinpath('is-en/base')
tuned_model_dir = working_dir.joinpath('is-en/tuned')
binarised_model_dir = working_dir.joinpath('is-en/binarised')

base_moses_ini = base_model_dir.joinpath('model/moses.ini')
base_phrase_table = base_model_dir.joinpath('model/phrase-table.gz')
base_reordering_table = base_model_dir.joinpath('model/reordering-table.wbe-msd-bidirectional-fe.gz')

tuned_moses_ini = tuned_model_dir.joinpath('moses.ini')

binarised_moses_ini = binarised_model_dir.joinpath('moses.ini')
binarised_phrase_table = binarised_model_dir.joinpath('phrase-table')
binarised_reordering_table = binarised_model_dir.joinpath('reordering-table')

Þjálfa

In [ ]:
!mkdir -p {base_model_dir}

path = is_parice_pipeline[TRAIN].parent.joinpath(TRAIN)

train_moses(base_model_dir, path, 'is', 'en', en_parice_pipeline[LM])

tail -f /work/is-en/base/training.out


Fínpússa

In [212]:
!mkdir -p {tuned_model_dir}

tune_moses(tuned_model_dir, is_parice_pipeline[VAL], en_parice_pipeline[VAL], base_moses_ini)

tail -f /work/is-en/tuned/tune.out
[]


PosixPath('/work/is-en/tuned')

Pakka saman

In [26]:
!mkdir -p {binarised_model_dir}

lm_in = en_parice_pipeline[LM]
lm_out = binarised_model_dir.joinpath('lm-en.blm')

prepare_binarisation(tuned_moses_ini, 
                     lm_in,
                     lm_out, 
                     binarised_moses_ini, 
                     binarised_phrase_table, 
                     binarised_reordering_table)
binarise_phrase_table(base_phrase_table, binarised_phrase_table)
binarise_reordering_table(base_reordering_table, binarised_reordering_table)

Used options:
	Text phrase table will be read from: /work/is-en/base/model/phrase-table.gz
	Output phrase table will be written to: /work/is-en/binarised/phrase-table.minphr
	Step size for source landmark phrases: 2^10=1024
	Source phrase fingerprint size: 16 bits / P(fp)=1.52588e-05
	Selected target phrase encoding: Huffman + PREnc
	Maxiumum allowed rank for PREnc: 100
	Number of score components in phrase table: 4
	Single Huffman code set for score components: no
	Using score quantization: no
	Explicitly included alignment information: yes
	Running with 80 threads

Pass 1/3: Creating hash function for rank assignment
..................................................[5000000]
..................................................[10000000]
..................................................[15000000]
..................................................[20000000]
..................................................[25000000]
..................................................[30000000]
........

Þýða test gögnin og meta þýðingu

In [226]:
is_parice_pipeline[TRANSLATED_IS_EN] = c.corpus_create_path(is_parice_pipeline[TEST], TRANSLATED_IS_EN)

translate_corpus(binarised_moses_ini,  is_parice_pipeline[TEST], is_parice_pipeline[TRANSLATED_IS_EN])
print(eval_translation(en_parice_pipeline[TEST], is_parice_pipeline[TRANSLATED_IS_EN]))

Defined parameters (per moses.ini or switch):
	config: /work/is-en/binarised/moses.ini 
	distortion-limit: 6 
	feature: UnknownWordPenalty WordPenalty PhrasePenalty PhraseDictionaryCompact name=TranslationModel0 num-features=4 path=/work/is-en/binarised/phrase-table input-factor=0 output-factor=0 LexicalReordering name=LexicalReordering0 num-features=6 type=wbe-msd-bidirectional-fe-allff input-factor=0 output-factor=0 path=/work/is-en/binarised/reordering-table Distortion KENLM name=LM0 factor=0 path=/work/data/parice/lm-blm.en order=3 
	input-factors: 0 
	mapping: 0 T 0 
	threads: 14 
	weight: LexicalReordering0= 0.0839657 0.0592771 0.116033 0.0510411 0.0145316 0.103368 Distortion0= -0.0145896 LM0= 0.11677 WordPenalty0= -0.187629 PhrasePenalty0= -0.0271079 TranslationModel0= 0.0655779 0.0246838 0.134754 0.000671537 UnknownWordPenalty0= 1 
line=UnknownWordPenalty
FeatureFunction: UnknownWordPenalty0 start: 0 end: 0
line=WordPenalty
FeatureFunction: WordPenalty0 start: 1 end: 1
line=Phr

Line 24: Collecting options took 0.464 seconds at moses/Manager.cpp Line 141
Line 18: Collecting options took 4.303 seconds at moses/Manager.cpp Line 141
Line 24: Search took 0.057 seconds
Line 24: Decision rule took 0.000 seconds total
Line 24: Additional reporting took 0.000 seconds total
Line 24: Translation took 0.521 seconds total
Translating: það er enginn á ferli . 
Line 25: Initialize search took 0.000 seconds total
Line 18: Search took 0.065 seconds
Line 18: Decision rule took 0.000 seconds total
Line 18: Additional reporting took 0.000 seconds total
Line 18: Translation took 4.369 seconds total
Translating: • vinnuveitandinn sýnir fram á að starfsmenn séu enn varðir fyrir skaðlegum áhrifum á heilbrigði og gegn öryggisáhættu , meðal annars með því að tryggja að leiðbein - ingum framleiðandans um örugga notkun , í samræmi við tilskipun ráðsins 93 / 42 / ebe frá 14. júní 1993 um lækningatæki ( 12 ) , sé fylgt , 
Line 26: Initialize search took 0.001 seconds total
Line 11: Collec

Line 37: Search took 0.157 seconds
Line 37: Decision rule took 0.000 seconds total
Line 37: Additional reporting took 0.000 seconds total
Line 37: Translation took 0.985 seconds total
Translating: sjósetningarbúnaður fyrir björgunarfleka 
Line 45: Initialize search took 0.000 seconds total
Line 22: Search took 0.311 seconds
Line 22: Decision rule took 0.000 seconds total
Line 22: Additional reporting took 0.000 seconds total
Line 22: Translation took 4.951 seconds total
Translating: lúxemborg 
Line 46: Initialize search took 0.000 seconds total
Line 46: Collecting options took 0.001 seconds at moses/Manager.cpp Line 141
Line 46: Search took 0.000 seconds
Line 46: Decision rule took 0.000 seconds total
Line 46: Additional reporting took 0.000 seconds total
Line 46: Translation took 0.001 seconds total
Translating: e 413 tragakant 
Line 47: Initialize search took 0.000 seconds total
Line 47: Collecting options took 0.012 seconds at moses/Manager.cpp Line 141
Line 47: Search took 0.001 se

Line 60: Collecting options took 0.476 seconds at moses/Manager.cpp Line 141
Line 60: Search took 0.020 seconds
Line 60: Decision rule took 0.000 seconds total
Line 60: Additional reporting took 0.000 seconds total
Line 60: Translation took 0.496 seconds total
Translating: útferð og kláði í augum , 
Line 64: Initialize search took 0.000 seconds total
Line 63: Collecting options took 0.217 seconds at moses/Manager.cpp Line 141
Line 61: Collecting options took 0.423 seconds at moses/Manager.cpp Line 141
Line 63: Search took 0.031 seconds
Line 63: Decision rule took 0.000 seconds total
Line 63: Additional reporting took 0.000 seconds total
Line 63: Translation took 0.248 seconds total
Translating: engin birta kemst inn . 
Line 65: Initialize search took 0.000 seconds total
Line 61: Search took 0.028 seconds
Line 61: Decision rule took 0.000 seconds total
Line 61: Additional reporting took 0.000 seconds total
Line 61: Translation took 0.451 seconds total
Translating: sýnatökustaðir skulu a

Line 83: Search took 0.022 seconds
Line 83: Decision rule took 0.000 seconds total
Line 83: Additional reporting took 0.000 seconds total
Line 83: Translation took 0.127 seconds total
Translating: þurrkuð , þynnt , unnin og samsett matvæli 
Line 86: Initialize search took 0.000 seconds total
Line 85: Collecting options took 0.026 seconds at moses/Manager.cpp Line 141
Line 86: Collecting options took 0.009 seconds at moses/Manager.cpp Line 141
Line 75: Collecting options took 1.333 seconds at moses/Manager.cpp Line 141
Line 48: Search took 0.496 seconds
Line 48: Decision rule took 0.000 seconds total
Line 48: Additional reporting took 0.000 seconds total
Line 48: Translation took 4.650 seconds total
Translating: þú ættir að gera það . 
Line 87: Initialize search took 0.000 seconds total
Line 75: Search took 0.044 seconds
Line 75: Decision rule took 0.000 seconds total
Line 75: Additional reporting took 0.000 seconds total
Line 75: Translation took 1.378 seconds total
Translating: sjaldg

...

Line 2916: Search took 0.221 seconds
Line 2916: Decision rule took 0.000 seconds total
Line 2916: Additional reporting took 0.000 seconds total
Line 2916: Translation took 0.819 seconds total
Translating: þegar aðildarríkin samþykkja þessar ráðstafanir skal vera í þeim tilvísun í þessa tilskipun eða þeim fylgja slík tilvísun þegar þær eru birtar opinberlega . aðildarríkin skulu setja nánari reglur um slíka tilvísun . 
Line 2941: Initialize search took 0.002 seconds total
Line 2939: Search took 0.109 seconds
Line 2939: Decision rule took 0.000 seconds total
Line 2939: Additional reporting took 0.000 seconds total
Line 2939: Translation took 0.125 seconds total
Translating: ég sel það bara . 
Line 2942: Initialize search took 0.000 seconds total
Line 2933: Search took 0.277 seconds
Line 2933: Decision rule took 0.000 seconds total
Line 2933: Additional reporting took 0.000 seconds total
Line 2933: Translation took 0.356 seconds total
Line 2930: Search took 0.443 seconds
Line 2930: Decisi

Line 2899: Search took 1.995 seconds
BEST TRANSLATION: the notified bodies that carry out the conformity assessment or assess the conformity or suitability for use of the verification of subsystems must coordinate their decisions as closely as possible , in particular in the absence of any european specification , of council directive 91/440/eec requires a separation of transport service operation and management járnbrautargrunnvirkjanna|UNK|UNK|UNK bound , respectively . [1111111111111111111111111111111111111111111111111111111111111111]  [total=-132.258] core=(-100.000,-59.000,24.000,-59.886,-238.267,-33.863,-131.290,-10.199,-7.069,-3.767,-17.469,-7.847,-0.578,-19.000,-220.238)  
BEST TRANSLATION: hello , sweetie . [1111]  [total=-1.377] core=(0.000,-4.000,1.000,-1.386,-4.464,-1.099,-3.264,-0.511,0.000,0.000,0.000,0.000,0.000,0.000,-14.608)  
BEST TRANSLATION: definition [1]  [total=-0.798] core=(0.000,-1.000,1.000,-0.401,-0.682,-0.109,-0.125,-0.088,0.000,0.000,0.000,0.000,0.000,0.000

Translating: ó , maður . 
Line 2974: Initialize search took 0.000 seconds total
Line 2945: Search took 1.162 seconds
Line 2945: Decision rule took 0.000 seconds total
Line 2945: Additional reporting took 0.000 seconds total
Line 2945: Translation took 1.401 seconds total
Line 2963: Search took 0.500 seconds
Line 2963: Decision rule took 0.000 seconds total
Line 2963: Additional reporting took 0.000 seconds total
Line 2963: Translation took 0.546 seconds total
Line 2974: Collecting options took 0.029 seconds at moses/Manager.cpp Line 141
Translating: og matvæli og reglur um heilbrigði og velferð dýra séu virt ( * ) . 
Line 2975: Initialize search took 0.001 seconds total
Translating: heiti innihaldsefnis 
Line 2976: Initialize search took 0.000 seconds total
Line 2976: Collecting options took 0.008 seconds at moses/Manager.cpp Line 141
Line 2976: Search took 0.002 seconds
Line 2976: Decision rule took 0.000 seconds total
Line 2976: Additional reporting took 0.000 seconds total
Line 2976

Line 2979: Search took 0.191 seconds
Line 2979: Decision rule took 0.000 seconds total
Line 2979: Additional reporting took 0.000 seconds total
Line 2979: Translation took 0.199 seconds total
Translating: „ bg : 
Line 2989: Initialize search took 0.000 seconds total
Line 2989: Collecting options took 0.001 seconds at moses/Manager.cpp Line 141
Line 2989: Search took 0.008 seconds
Line 2989: Decision rule took 0.000 seconds total
Line 2989: Additional reporting took 0.000 seconds total
Line 2989: Translation took 0.009 seconds total
Translating: stefnumót stefnumót þetta er gott til að afrafmagna . 
Line 2990: Initialize search took 0.000 seconds total
Line 2988: Collecting options took 0.043 seconds at moses/Manager.cpp Line 141
Line 2964: Search took 0.338 seconds
Line 2964: Decision rule took 0.000 seconds total
Line 2964: Additional reporting took 0.000 seconds total
Line 2964: Translation took 0.793 seconds total
Translating: athugið eftirfarandi áður en byrjað er á þrepi 4 : 
Line

Line 2998: Search took 0.472 seconds
BEST TRANSLATION: in clinical trials of 118 children and adolescents 3 to 16 years of age ) , 6 % discontinued therapy due to adverse events . [1111111111111111111111]  [total=-4.470] core=(0.000,-25.000,6.000,-1.454,-28.940,-6.279,-32.369,-3.191,0.000,0.000,-1.132,0.000,0.000,0.000,-59.901)  
BEST TRANSLATION: who is he ? [1111]  [total=-0.903] core=(0.000,-4.000,1.000,-0.405,-2.414,-0.723,-3.260,-0.093,0.000,0.000,0.000,0.000,0.000,0.000,-12.269)  
Line 2998: Decision rule took 0.000 seconds total
Line 2998: Additional reporting took 0.000 seconds total
Line 2998: Translation took 0.624 seconds total
Name:moses	VmPeak:4849724 kB	VmRSS:2775996 kB	RSSMax:4137072 kB	user:1404.876	sys:137.796	CPU:1542.673	real:114.170
['perl: warning: Setting locale failed.', 'perl: warning: Please check that your locale settings:', '\tLANGUAGE = "en_US:en",', '\tLC_ALL = (unset),', '\tLC_CTYPE = "C.UTF-8",', '\tLANG = "en_US.UTF-8"', '    are supported and installed 

In [11]:
def translate_is_en(moses_ini, sentence):
    sentence = c.sent_process_v1(sentence, c.Lang.IS)
    !echo "{sentence}" | {os.getenv('MOSESDECODER')}/bin/moses -f {moses_ini}

In [12]:
sentence = "Ég man ekki eftir neinum góðum myndum nýlega "
print(translate_is_en(binarised_moses_ini, sentence))

Defined parameters (per moses.ini or switch):
	config: /work/is-en/binarised/moses.ini 
	distortion-limit: 6 
	feature: UnknownWordPenalty WordPenalty PhrasePenalty PhraseDictionaryCompact name=TranslationModel0 num-features=4 path=/work/is-en/binarised/phrase-table input-factor=0 output-factor=0 LexicalReordering name=LexicalReordering0 num-features=6 type=wbe-msd-bidirectional-fe-allff input-factor=0 output-factor=0 path=/work/is-en/binarised/reordering-table Distortion KENLM name=LM0 factor=0 path=/work/data/parice/lm-blm.en order=3 
	input-factors: 0 
	mapping: 0 T 0 
	threads: 14 
	weight: LexicalReordering0= 0.0839657 0.0592771 0.116033 0.0510411 0.0145316 0.103368 Distortion0= -0.0145896 LM0= 0.11677 WordPenalty0= -0.187629 PhrasePenalty0= -0.0271079 TranslationModel0= 0.0655779 0.0246838 0.134754 0.000671537 UnknownWordPenalty0= 1 
line=UnknownWordPenalty
FeatureFunction: UnknownWordPenalty0 start: 0 end: 0
line=WordPenalty
FeatureFunction: WordPenalty0 start: 1 end: 1
line=Phr

In [13]:
sentence = "já, einmitt"
print(translate_is_en(binarised_moses_ini, sentence))

Defined parameters (per moses.ini or switch):
	config: /work/is-en/binarised/moses.ini 
	distortion-limit: 6 
	feature: UnknownWordPenalty WordPenalty PhrasePenalty PhraseDictionaryCompact name=TranslationModel0 num-features=4 path=/work/is-en/binarised/phrase-table input-factor=0 output-factor=0 LexicalReordering name=LexicalReordering0 num-features=6 type=wbe-msd-bidirectional-fe-allff input-factor=0 output-factor=0 path=/work/is-en/binarised/reordering-table Distortion KENLM name=LM0 factor=0 path=/work/data/parice/lm-blm.en order=3 
	input-factors: 0 
	mapping: 0 T 0 
	threads: 14 
	weight: LexicalReordering0= 0.0839657 0.0592771 0.116033 0.0510411 0.0145316 0.103368 Distortion0= -0.0145896 LM0= 0.11677 WordPenalty0= -0.187629 PhrasePenalty0= -0.0271079 TranslationModel0= 0.0655779 0.0246838 0.134754 0.000671537 UnknownWordPenalty0= 1 
line=UnknownWordPenalty
FeatureFunction: UnknownWordPenalty0 start: 0 end: 0
line=WordPenalty
FeatureFunction: WordPenalty0 start: 1 end: 1
line=Phr